In [1]:
import xml.etree.ElementTree as ElementTree

class XmlListConfig(list):
    def __init__(self, aList):
        for element in aList:
            if element:
                # treat like dict
                if len(element) == 1 or element[0].tag != element[1].tag:
                    self.append(XmlDictConfig(element))
                # treat like list
                elif element[0].tag == element[1].tag:
                    self.append(XmlListConfig(element))
            elif element.text:
                text = element.text.strip()
                if text:
                    self.append(text)


class XmlDictConfig(dict):
    def __init__(self, parent_element):
        if parent_element.items():
            self.updateShim( dict(parent_element.items()) )
        for element in parent_element:
            if len(element):
                aDict = XmlDictConfig(element)
            #   if element.items():
            #   aDict.updateShim(dict(element.items()))
                self.updateShim({element.tag: aDict})
            elif element.items():    # items() is specialy for attribtes
                elementattrib= element.items()
                if element.text:           
                    elementattrib.append((element.tag,element.text ))     # add tag:text if there exist
                self.updateShim({element.tag: dict(elementattrib)})
            else:
                self.updateShim({element.tag: element.text})

    def updateShim (self, aDict ):
        for key in aDict.keys():   # keys() includes tag and attributes
            if key in self:
                value = self.pop(key)
                if type(value) is not list:
                    listOfDicts = []
                    listOfDicts.append(value)
                    listOfDicts.append(aDict[key])
                    self.update({key: listOfDicts})
                else:
                    value.append(aDict[key])
                    self.update({key: value})
            else:
                self.update({key:aDict[key]})



In [2]:
!pip install xmltodict

In [26]:
import xml.etree.ElementTree as ElementTree

import xmltodict
import pprint
import json
import pandas as pd
import numpy as np



#tree = ElementTree.parse('sample.xml')
tree = ElementTree.parse('./raw/BUILT.30.experienced_plans.xml')
root = tree.getroot()
xmldict = XmlDictConfig(root)

xmldict['person']


[{'id': '0',
  'plan': {'score': '-132.96673121955368',
   'selected': 'yes',
   'leg': [{'mode': 'bike',
     'dep_time': '09:03:00',
     'trav_time': '01:18:16',
     'route': {'type': 'generic',
      'start_link': '226193928_0',
      'end_link': '420514148_1',
      'trav_time': '01:18:16',
      'distance': '19569.08484854245'}},
    {'mode': 'bike',
     'dep_time': '13:31:16',
     'trav_time': '00:05:11',
     'route': {'type': 'generic',
      'start_link': '420514148_1',
      'end_link': '458166896_5',
      'trav_time': '00:05:11',
      'distance': '1298.736213671756'}},
    {'mode': 'bike',
     'dep_time': '13:42:27',
     'trav_time': '00:09:46',
     'route': {'type': 'generic',
      'start_link': '458166896_5',
      'end_link': '588168464_0',
      'trav_time': '00:09:46',
      'distance': '2445.0770476881826'}},
    {'mode': 'bike',
     'dep_time': '18:52:13',
     'trav_time': '01:20:43',
     'route': {'type': 'generic',
      'start_link': '588168464_0',
   

In [37]:
# keep

id_data = []
activity_data = []
mode_data = []
one_column = []

# for row in xmldict['person']:
#     print(row['plan']['leg'])

for row in xmldict['person']:
    #print(row['id'])
    id_data.append(row['id'])
    #print(row['plan']['activity'])
    activity_data.append(row['plan']['activity'])
    # Teresa: error handling
    one_column.append(row['plan']['activity'])
    #one_column.append(row['plan']['leg'])

    try:
        one_column.append(row['plan']['leg'])
        mode_data.append(row['plan']['leg'])
    except KeyError:
        one_column.append('skip')
        continue
    
# data_tuples = list(zip(id_data, activity_data, mode_data))

#-----------------------
# print(id_data[2])
# print(activity_data[2][1]['type'])
#print(len(mode_data[2]))
#print(mode_data[2])


In [38]:
one_column

[[{'type': 'Work',
   'link': '226193928_0',
   'end_time': '09:03:00',
   'activity': '\n\t\t\t'},
  {'type': 'Work',
   'link': '420514148_1',
   'start_time': '10:21:16',
   'end_time': '13:31:16',
   'activity': '\n\t\t\t'},
  {'type': 'Secondary',
   'link': '458166896_5',
   'start_time': '13:36:27',
   'end_time': '13:42:27',
   'activity': '\n\t\t\t'},
  {'type': 'Work',
   'link': '588168464_0',
   'start_time': '13:52:13',
   'end_time': '18:52:13',
   'activity': '\n\t\t\t'},
  {'type': 'Home',
   'link': '226193928_0',
   'start_time': '20:12:56',
   'activity': '\n\t\t\t'}],
 [{'mode': 'bike',
   'dep_time': '09:03:00',
   'trav_time': '01:18:16',
   'route': {'type': 'generic',
    'start_link': '226193928_0',
    'end_link': '420514148_1',
    'trav_time': '01:18:16',
    'distance': '19569.08484854245'}},
  {'mode': 'bike',
   'dep_time': '13:31:16',
   'trav_time': '00:05:11',
   'route': {'type': 'generic',
    'start_link': '420514148_1',
    'end_link': '458166896_5

In [6]:
mode_data[0]

[{'mode': 'bike',
  'dep_time': '09:03:00',
  'trav_time': '01:18:16',
  'route': {'type': 'generic',
   'start_link': '226193928_0',
   'end_link': '420514148_1',
   'trav_time': '01:18:16',
   'distance': '19569.08484854245'}},
 {'mode': 'bike',
  'dep_time': '13:31:16',
  'trav_time': '00:05:11',
  'route': {'type': 'generic',
   'start_link': '420514148_1',
   'end_link': '458166896_5',
   'trav_time': '00:05:11',
   'distance': '1298.736213671756'}},
 {'mode': 'bike',
  'dep_time': '13:42:27',
  'trav_time': '00:09:46',
  'route': {'type': 'generic',
   'start_link': '458166896_5',
   'end_link': '588168464_0',
   'trav_time': '00:09:46',
   'distance': '2445.0770476881826'}},
 {'mode': 'bike',
  'dep_time': '18:52:13',
  'trav_time': '01:20:43',
  'route': {'type': 'generic',
   'start_link': '588168464_0',
   'end_link': '226193928_0',
   'trav_time': '01:20:43',
   'distance': '20180.827077682676'}}]

In [41]:
## keep finish separating 
##need to change print to add
mode = ['walk','bike','car','taxi']
act = ['Home','Secondary','Work','University','School']
new_list=[]
mode_mode_data = []
id_id_data=[]
activity_list = pd.DataFrame(columns=['type' , 'link', 'start_time' , 'end_time','activity'])



pt_count=0;
start = 0;
for i in range(0,10): #len(activity_data)
    start = 0;
    
#Teresa: added error handling
#     try :
#         key = mode_data[i]
#     except KeyError:
#         continue
    #print(id_data[i])
    
    for j in range(0,len(activity_data[i])):
        pt_count=0

        if (activity_data[i][j]['type'] in act):
            #print(activity_data[i][j])
            id_id_data.append(id_data[i])
            #act_activity_data.append(activity_data[i][j]['type'])

            ###add activity to list
            new_list.append(activity_data[i][j])
            #print(new_list)
            
            ### append list to DataFrame
            activity_list= activity_list.append(new_list, ignore_index=True)
            new_list.clear()


#Teresa: the k loop should not be an inner loop of j loop (it doesn't use j index)
#Seems the type 'car' has different format? you can skip it by using 'try...except...continue' at the outer i loop

#Mina: I kept it in k look because I wanted to keep track of ID as the same number of rows as the Mode.
#If not, it will have shorteer rows.
        for k in range(start,len(mode_data[i])):
        
            try :
                key = mode_data[i][k]
            except KeyError:
                print(mode_data[i])
                mode_mode_data.append('skip')
                continue
#             print(i,k)
#             print(mode_data[i][k])
            if mode_data[i][k]['mode'] in mode:
                mode_mode_data.append(mode_data[i][k]['mode'])
                #print(i,j,k,mode_data[i][k])
                start=k+1;
                break;

            elif mode_data[i][k]['mode']=='pt': 
                if(pt_count ==0):
                    mode_mode_data.append(mode_data[i][k]['mode'])
                    #print(i,j,k,mode_data[i][k])
                    pt_count=1 
            elif mode_data[i][k]['mode']=='egress_walk' and pt_count==1:
                start = k+1;
                break;

            else:
                continue;


    



    mode_mode_data.append('')
    
    
print("data mining done")


{'mode': 'car', 'dep_time': '06:03:00', 'trav_time': '00:21:23', 'route': {'type': 'links', 'start_link': '5671084_0', 'end_link': '8948920_0', 'trav_time': '00:21:23', 'distance': '29089.532874252345', 'route': '5671084_0 195743195_0 195743195_1 195743195_2 226193905_0_r 46165816_0_r 438363728_0_r 413052676_0 195743264_0 438900013_0 438900013_1 420809440_0 195743228_0 421832645_0 222299274_0 195743229_0 195743226_0 516664210_0 516664206_0 413050334_0 413050334_1 413050334_2 413050334_3 496982371_0 588157330_0 438370108_0 420809441_0 420809420_0 420809420_1 420809420_2 420809420_3 195743557_0 195743558_0 195743558_1 195743558_2 195743558_3 420522049_0 420522049_1 420522049_2 420522049_3 473884145_0 505776502_0 22903923_0 34625442_0 194923802_0 194923802_1 194923802_2 194923801_0 464847780_0 34625463_0 194923804_0 22903913_0 194923803_0 118714476_0 118714476_1 118714476_2 118714476_3 118714476_4 194926850_0 421853810_0 421853810_1 421853810_2 421853809_0 68325061_0 68325061_1 421853647_

In [43]:
#id and mode data tuple
data_tuples = list(zip(id_id_data, mode_mode_data))

data_tuples

#keep -make a DataFrame

df = pd.DataFrame(data_tuples, columns=['id','mode'])



df
print("dataframe succeed")

dataframe succeed


In [44]:
#merge index list and activity list

df_merged = pd.concat([df, activity_list], axis=1)
df_merged


id  mode       type         link start_time  end_time  activity
0         0  bike       Work  226193928_0        NaN  09:03:00  \n\t\t\t
1         0  bike       Work  420514148_1   10:21:16  13:31:16  \n\t\t\t
2         0  bike  Secondary  458166896_5   13:36:27  13:42:27  \n\t\t\t
3         0  bike       Work  588168464_0   13:52:13  18:52:13  \n\t\t\t
4         0             Home  226193928_0   20:12:56       NaN  \n\t\t\t
5         1  skip       Home    5671084_0        NaN  06:03:00  \n\t\t\t
6         1  skip       Work    8948920_0   06:24:23  11:53:23  \n\t\t\t
7   1007981  skip       Home  421854005_0        NaN  07:52:00  \n\t\t\t
8   1007981  skip  Secondary   46694764_3   08:14:39  08:19:39  \n\t\t\t
9   1007981  skip       Work  438384693_1   12:37:14  22:54:14  \n\t\t\t
10  1007982  skip       Home   46694766_1        NaN  07:45:00  \n\t\t\t
11  1007982  skip       Work  412180553_0   18:39:48  22:09:48  \n\t\t\t
12  1007983  skip       Home   46694766_0        NaN  07:52:00  \n\t\t\t
13  1007983        Secondary   46694766_2   08:33:30  08:38:30  \n\t\t\t
14  1007983  walk       Work    5673063_9   12:57:17  23:14:17  \n\t\t\t
15  1007984             Home    5670707_8        NaN  07:52:00  \n\t\t\t
16  1007984  skip  Secondary   46334580_4   08:44:57  08:49:57  \n\t\t\t
17  1007984  skip       Work  420356173_0   13:21:39  23:38:39  \n\t\t\t
18  1007985  skip       Home  421853988_0        NaN  07:45:00  \n\t\t\t
19  1007985  skip       Work   22898269_2   18:15:37  21:45:37  \n\t\t\t
20  1007986  skip       Home  460657164_3        NaN  07:29:00  \n\t\t\t
21  1007986  skip  Secondary  588157329_1   20:28:54  20:33:54  \n\t\t\t
22  1007986  skip       Work    5670657_0   20:51:28       NaN  \n\t\t\t
23  1007987  skip       Home    5672135_0        NaN  07:29:00  \n\t\t\t
24  1007987        Secondary  588157329_3   20:04:14  20:09:14  \n\t\t\t
25  1007987  walk       Work   32934343_0   20:44:12       NaN  \n\t\t\t
26  1007988  walk       Home  421854000_0        NaN  16:04:00  \n\t\t\t
27  1007988        Secondary    5670797_8   16:12:03  16:16:03  \n\t\t\t
28  1007988        Secondary  421853952_0   16:26:26  16:29:26  \n\t\t\t
29  1007988  skip  Secondary  569266484_3   16:38:30  17:47:30  \n\t\t\t
30  1007988  skip  Secondary  421853953_0   17:56:04  18:02:04  \n\t\t\t
31  1007988  skip       Home  421854000_0   18:15:50       NaN  \n\t\t\t

In [17]:
df_merged['start_time']=pd.to_datetime(df_merged['start_time'])
df_merged['end_time']=pd.to_datetime(df_merged['end_time'])


#df_merged['end_time']=pd.to_datetime(df_merged['end_time'],format= '%H:%M:%S' ).dt.time





In [18]:
# check travel time
trave_time = pd.DataFrame(columns={'id','travel_time'})

for i in range(0,len(df_merged)-1):
    if(df_merged.iloc[i]['id']==df_merged.iloc[i+1]['id']):
        diff =pd.Timedelta(df_merged.iloc[i]['end_time']  - df_merged.iloc[i+1]['start_time'] ).seconds / 3600
    else:
        diff = np.nan
    
    trave_time=trave_time.append([{'id': df_merged.iloc[i]['id'], 'travel_time':diff}], ignore_index=True)




In [21]:
#merge 

df_final =  pd.concat([df_merged, trave_time['travel_time']], axis=1)
df_final

id  mode       type         link          start_time  \
0         0  walk       Work  226193928_0                 NaT   
1         0  walk       Work  420514148_1 2019-04-21 15:34:22   
2         0  walk  Secondary  458166896_5 2019-04-21 19:10:20   
3         0             Work  588168464_0 2019-04-21 20:05:14   
4         1   car       Home    5671084_0                 NaT   
5         1    pt       Work    8948920_0 2019-04-21 06:24:23   
6         1  walk       Work    5670719_4 2019-04-21 14:25:05   
7         1  walk  Secondary   68668519_0 2019-04-21 17:17:39   
8         1             Work  630828584_1 2019-04-21 19:04:56   
9   1007981  walk       Home  421854005_0                 NaT   
10  1007981    pt  Secondary   46694764_3 2019-04-21 08:14:39   
11  1007981             Work  438384693_1 2019-04-21 09:30:05   
12  1007982    pt       Home   46694766_1                 NaT   
13  1007982    pt       Work  412180553_0 2019-04-21 08:42:39   
14  1007982    pt  Secondary  570164048_0 2019-04-21 13:23:25   
15  1007982    pt       Work   46171883_0 2019-04-21 15:13:16   
16  1007982  walk  Secondary  226041022_0 2019-04-21 18:53:22   
17  1007982  walk  Secondary  460585328_1 2019-04-21 20:55:24   
18  1007982        Secondary  226041027_2 2019-04-21 23:29:07   
19  1007983  walk       Home   46694766_0                 NaT   
20  1007983    pt  Secondary   46694766_2 2019-04-21 08:33:30   
21  1007983  walk       Work    5673063_9 2019-04-21 09:48:47   
22  1007983        Secondary  542215781_0 2019-04-21 23:16:10   
23  1007984  walk       Home    5670707_8                 NaT   
24  1007984    pt  Secondary   46334580_4 2019-04-21 08:44:56   
25  1007984             Work  420356173_0 2019-04-21 09:50:18   
26  1007985    pt       Home  421853988_0                 NaT   
27  1007985    pt       Work   22898269_2 2019-04-21 08:50:24   
28  1007985    pt  Secondary   46594129_0 2019-04-21 13:18:33   
29  1007985    pt       Work  413045201_0 2019-04-21 15:00:29   
30  1007985  walk  Secondary  226041022_0 2019-04-21 18:33:57   
31  1007985  walk  Secondary   46522008_4 2019-04-21 20:32:41   
32  1007985        Secondary  258619239_0 2019-04-21 22:56:38   
33  1007986    pt       Home  460657164_3                 NaT   
34  1007986  walk  Secondary  588157329_1 2019-04-21 08:33:27   
35  1007986  walk       Work    5670657_0 2019-04-21 08:56:01   
36  1007986    pt  Secondary    5670092_3 2019-04-21 20:41:56   
37  1007986        Secondary    5670771_0 2019-04-21 22:18:16   
38  1007987    pt       Home    5672135_0                 NaT   
39  1007987  walk  Secondary  588157329_3 2019-04-21 08:54:19   
40  1007987  walk       Work   32934343_0 2019-04-21 09:34:17   
41  1007987    pt  Secondary    5670366_7 2019-04-21 21:30:38   
42  1007987        Secondary   68668537_0 2019-04-21 22:54:02   
43  1007988  walk       Home  421854000_0                 NaT   
44  1007988  walk  Secondary    5670797_8 2019-04-21 16:17:40   
45  1007988    pt  Secondary  421853952_0 2019-04-21 17:06:51   
46  1007988  walk  Secondary  569266484_3 2019-04-21 18:01:07   
47  1007988  walk  Secondary  421853953_0 2019-04-21 20:24:42   
48  1007988             Home  421854000_0 2019-04-21 20:51:44   

              end_time  activity  travel_time  
0  2019-04-21 09:03:00  \n\t\t\t    17.477222  
1  2019-04-21 18:44:22  \n\t\t\t    23.567222  
2  2019-04-21 19:16:20  \n\t\t\t    23.185000  
3                  NaT  \n\t\t\t          NaN  
4  2019-04-21 06:03:00  \n\t\t\t    23.643611  
5  2019-04-21 11:53:23  \n\t\t\t    21.471667  
6  2019-04-21 16:38:05  \n\t\t\t    23.340556  
7  2019-04-21 18:26:39  \n\t\t\t    23.361944  
8                  NaT  \n\t\t\t          NaN  
9  2019-04-21 07:52:00  \n\t\t\t    23.622500  
10 2019-04-21 08:19:39  \n\t\t\t    22.826111  
11 2019-04-21 19:47:05  \n\t\t\t          NaN  
12 2019-04-21 07:45:00  \n\t\t\t    23.039167  
13 2019-04-21 12:12:39  \n\t\t\t    22.820556  
14 2019-04-21 14:08:25  \n\t\t\t    22

In [19]:
#group by id for travel_time

####### add mode on the final group by
total_travel_time = df_final.groupby(['id']).sum()
total_travel_time

#len(travel_time_comparison)

NameError: name 'df_final' is not defined

In [20]:
df_final.to_excel("10th_mode_final.xlsx")



NameError: name 'df_final' is not defined

In [257]:
total_travel_time.to_excel("10th_totalTime_final.xlsx")
#df_merged.to_csv("sample2.csv",sep='\t', encoding='utf-8')
print("all done")

all done
